In [1]:
# Import necessary packages
using CSV, DataFrames, Plots, Random, DecisionTree, Statistics, LinearAlgebra, JuMP, Gurobi, StatsBase

# Set random seed for reproducibility
Random.seed!(1234)

TaskLocalRNG()

In [4]:
# Step 1: Load the data
# ---------------------

# Load the continuous target data (log_growth)
data_continuous = CSV.read("data_continuous_target.csv", DataFrame)

# Load the binary target data (binary success)
data_binary = CSV.read("data_binary_target.csv", DataFrame);

In [5]:
data_binary

7499×92 DataFrame
  Row │ Number of Founders  Series A Money Raised (in USD)  Number of Seed/Pre ⋯
      │ Float64             Float64                         Float64            ⋯
──────┼─────────────────────────────────────────────────────────────────────────
    1 │             2.3379                       1.29272e7                     ⋯
    2 │             2.3379                       1.29272e7
    3 │             1.0                          1.1e6
    4 │             1.0                          3.5e6
    5 │             2.3379                  497000.0                           ⋯
    6 │             2.0                          8.77623e6
    7 │             3.0                          1.29272e7
    8 │             2.0                          1.29272e7
    9 │             1.0                          1.29e6                        ⋯
   10 │             1.0                          5.0e6
   11 │             1.0                          5.0e6
  ⋮   │         ⋮                         ⋮                               ⋮    ⋱
 7490 │             5.0                          2.0e7
 7491 │             3.0                          1.1e7                         ⋯
 7492 │             1.0                          1.29272e7
 7493 │             2.3379                       1.29272e7
 7494 │             2.0                          1.29272e7
 7495 │             2.0                          3.11e7                        ⋯
 7496 │             2.0                          1.2e7
 7497 │             1.0                          1.7e7
 7498 │             1.0                          5.9e7
 7499 │             2.0                          2.15e7                        ⋯
                                                90 columns and 7478 rows omitted

In [6]:
# Step 2: Split the data into train and test sets
# -----------------------------------------------

# Number of rows in the dataset
n = nrow(data_continuous)

# Create a random permutation of indices
indices = shuffle(1:n)

# Split indices into 80% train and 20% test
train_size = Int(floor(0.8 * n))
train_indices = indices[1:train_size]
test_indices = indices[train_size+1:end]

# Split data_continuous
train_data_continuous = data_continuous[train_indices, :]
test_data_continuous = data_continuous[test_indices, :]

# Split data_binary
train_data_binary = data_binary[train_indices, :]
test_data_binary = data_binary[test_indices, :];

# Predictions

In [7]:
# Step 3: Train an optimal classification tree on the binary target
# -----------------------------------------------------------------

# Exclude the target variable 'Success' to get features
X_train_binary = select(train_data_binary, Not("Success"))
y_train_binary = train_data_binary[:, "Success"]

# Similarly for the test set
X_test_binary = select(test_data_binary, Not("Success"))
y_test_binary = test_data_binary[:, "Success"]

# Set up the optimal classification tree learner
grid_binary = IAI.GridSearch(
    IAI.OptimalTreeClassifier(
        random_seed=1,
        minbucket=200,
    ),
    max_depth=1:5,
)
IAI.fit!(grid_binary, X_train_binary, y_train_binary)
learner_binary = IAI.get_learner(grid_binary)

[ Warning: This copy of Interpretable AI software is for academic purposes only and not for commercial use.
┌ Warning: Interpretable AI license expires soon: 2024-12-31T00:00:00. If you need to renew, please send us the following machine ID:
└ 53077424a9cbcf71e2d64b8c59d89da63dd637c8c8134220a6ff8190ae449d2f


Fitted OptimalTreeClassifier:
  1) Split: Earliest Funding Round - Number of Funding Rounds < 4.5
    2) Split: Days Between Founding and Series B < 1293.5
      3) Split: Earliest Funding Round - Number of Funding Rounds < 2.5
        4) Predict: 0 (64.92%), [161,87], 248 points, error 0.3508
        5) Predict: 1 (64.11%), [239,427], 666 points, error 0.3589
      6) Predict: 0 (68.39%), [1136,525], 1661 points, error 0.3161
    7) Split: Days Between Founding and Series B < 2467
      8) Split: Days Between Founding and First Seed/Pre-Seed < 1770.5
        9) Predict: 1 (72.54%), [694,1833], 2527 points, error 0.2746
        10) Predict: 0 (54.88%), [135,111], 246 points, error 0.4512
      11) Predict: 0 (65.90%), [429,222], 651 points, error 0.341

In [8]:
IAI.score(grid_binary, X_train_binary, y_train_binary, criterion=:misclassification)

0.6869478246374396

In [9]:
IAI.score(grid_binary, X_test_binary, y_test_binary, criterion=:auc)

0.7002841138537362

In [10]:
roc = IAI.ROCCurve(grid_binary, X_test_binary, y_test_binary, positive_label=1)

ROCCurve with AUC 0.7003:

 Row │ threshold  tpr       fpr      
     │ Float64    Float64   Float64  
─────┼───────────────────────────────
   1 │  1.0       0.0       0.0
   2 │  0.725366  0.586877  0.249631
   3 │  0.641141  0.699878  0.363368
   4 │  0.45122   0.73633   0.420975
   5 │  0.350806  0.773998  0.469719
   6 │  0.341014  0.845687  0.590842
   7 │  0.316075  1.0       1.0
   8 │  0.0       1.0       1.0

In [11]:
# Step 4: Train an optimal regression tree on the continuous target
# -----------------------------------------------------------------

# Exclude the target variable 'log_growth' to get features
X_train_continuous = select(train_data_continuous, Not("log_growth"))
y_train_continuous = train_data_continuous[:, "log_growth"]

# Similarly for the test set
X_test_continuous = select(test_data_continuous, Not("log_growth"))
y_test_continuous = test_data_continuous[:, "log_growth"]

# Set up the optimal regression tree learner
grid_continuous = IAI.GridSearch(
    IAI.OptimalTreeRegressor(
        random_seed=123,
        minbucket=200,
    ),
    max_depth=1:5,
)
IAI.fit!(grid_continuous, X_train_continuous, y_train_continuous)
learner_continuous = IAI.get_learner(grid_continuous)

Fitted OptimalTreeRegressor:
  1) Split: Total Money Raised Before Series B < 2028913
    2) Split: Total Money Raised Before Series B < 6000
      3) Predict: 0.6931, 852 points, error 0
      4) Split: Earliest Funding Round - Number of Funding Rounds < 4.5
        5) Predict: 2.215, 205 points, error 1.445
        6) Predict: 3.085, 246 points, error 1.851
    7) Split: Earliest Funding Round - Number of Funding Rounds < 6.5
      8) Split: Number of Seed/Pre-Seed Rounds < 0.5
        9) Split: Earliest Funding Round - Number of Funding Rounds < 3.5
          10) Split: Earliest Funding Round - Number of Funding Rounds < 2.5
            11) Predict: 1.422, 292 points, error 0.1865
            12) Predict: 1.708, 373 points, error 0.3186
          13) Split: Days Between Founding and Series B < 1081.5
            14) Predict: 2.345, 240 points, error 0.5539
            15) Predict: 1.942, 506 points, error 0.5353
        16) Split: Earliest Funding Round - Number of Funding Rounds < 4.5
          17) Split: Total Money Raised Before Series B < 7009000
            18) Predict: 1.752, 201 points, error 0.5515
            19) Predict: 1.459, 614 points, error 0.1655
          20) Split: Days Between Founding and First Seed/Pre-Seed < 1121.5
            21) Predict: 2.036, 350 points, error 0.4968
            22) Predict: 1.645, 603 points, error 0.3558
      23) Split: Days Between Founding and Series B < 1702
        24) Split: Total Money Raised Before Series B < 11575000
          25) Split: Earliest Funding Round - Number of Funding Rounds < 8.5
            26) Predict: 2.724, 230 points, error 0.7304
            27) Predict: 3.344, 217 points, error 1.149
          28) Predict: 2.464, 344 points, error 0.7177
        29) Split: Days Between Founding and First Seed/Pre-Seed < 1784
          30) Predict: 2.269, 395 points, error 0.9411
          31) Predict: 1.711, 331 points, error 0.4915

In [12]:
# R^2 of training set
IAI.score(grid_continuous, X_train_continuous, y_train_continuous, criterion=:mse)

0.45997887451775965

In [13]:
# R^2 of testing set
IAI.score(grid_continuous, X_test_continuous, y_test_continuous, criterion=:mse)

0.45587072174008947

# Prescriptions

## Find Uncertain Parameters (p and r)

In [14]:
# Step 1: Apply the learner to get leaf indices for both training and test data
leaf_indices_continuous_train = IAI.apply(learner_continuous, X_train_continuous)
leaf_indices_continuous_test = IAI.apply(learner_continuous, X_test_continuous)

leaf_indices_binary_train = IAI.apply(learner_binary, X_train_binary)
leaf_indices_binary_test = IAI.apply(learner_binary, X_test_binary)

# Step 2: Add leaf indices as a new column in both training and test data
train_data_continuous.Leaf_continuous = leaf_indices_continuous_train
test_data_continuous.Leaf_continuous = leaf_indices_continuous_test

train_data_binary.Leaf_binary = leaf_indices_binary_train
test_data_binary.Leaf_binary = leaf_indices_binary_test

# Step 3: For each test data point, find training data points in the same leaf
# Continuous Tree
r_similar = [
    train_data_continuous[train_data_continuous.Leaf_continuous .== test_data_continuous.Leaf_continuous[i], :log_growth]
    for i in 1:size(test_data_continuous, 1)
]

# Binary Tree
p_similar = [
    train_data_binary[train_data_binary.Leaf_binary .== test_data_binary.Leaf_binary[i], :Success]
    for i in 1:size(test_data_binary, 1)
]


# Length of vector for each point
r_length = [length(x) for x in r_similar]
p_length = [length(x) for x in p_similar];

In [21]:
point_pred_p = IAI.predict(learner_binary, X_test_binary)
point_pred_r = IAI.predict(learner_continuous, X_test_continuous);

In [27]:
train_data_continuous

5999×93 DataFrame
  Row │ Number of Founders  Series A Money Raised (in USD)  Number of Seed/Pre ⋯
      │ Float64             Float64                         Float64            ⋯
──────┼─────────────────────────────────────────────────────────────────────────
    1 │                3.0                       1.29272e7                     ⋯
    2 │                2.0                       1.29272e7
    3 │                2.0                       1.29272e7
    4 │                2.0                       1.5e6
    5 │                1.0                       6.0e7                         ⋯
    6 │                1.0                       1.9e7
    7 │                5.0                       5.0e6
    8 │                3.0                       7.4e6
    9 │                1.0                       1.5e7                         ⋯
   10 │                1.0                       7.0e6
   11 │                3.0                       1.3e7
  ⋮   │         ⋮                         ⋮                               ⋮    ⋱
 5990 │                3.0                       1.29272e7
 5991 │                2.0                       1.29272e7                     ⋯
 5992 │                6.0                       5.5e6
 5993 │                3.0                       4.29183e6
 5994 │                4.0                       2.0e6
 5995 │                1.0                       1.29272e7                     ⋯
 5996 │                1.0                       1.29272e7
 5997 │                3.0                       1.5e7
 5998 │                4.0                       7.5e6
 5999 │                1.0                       5.0e6                         ⋯
                                                91 columns and 5978 rows omitted

In [24]:
point_pred_r

1500-element Vector{Float64}:
 2.2688058642423363
 2.4640757565644855
 1.4222235123811346
 2.723822325786875
 1.6446647730637167
 1.7114048909030881
 1.708200379943444
 1.6446647730637167
 1.708200379943444
 1.7521358889999736
 1.6446647730637167
 2.035930997368805
 1.4586513331256161
 ⋮
 2.2688058642423363
 2.2688058642423363
 1.708200379943444
 1.4586513331256161
 1.6446647730637167
 1.708200379943444
 0.6931471805599453
 1.708200379943444
 1.6446647730637167
 2.345049382727368
 2.2688058642423363
 1.9424869381541008

## Constants

In [14]:
#Constants
n= 1500
B = 1000;
N_lower = 10
N_upper = 50
M = 1000000

#amount a company raised in series b (we are assuming that is the target a startup says they want to raise. so 1 VC doesn't invest more than a startup is even asking for)
#that info isn't in Maxime's most recent, clean, "success" dataset he sent. Also, company id isn't in here. So I can't bring it in myself.
#For now, I can say don't invest more in a company than total money they've raised before series B.
#But no, I can't while using budget of 1000. I can do this once I increase budget to 50 million.
money_raised_before_seriesB =  X_test_binary[:,7];

## Point Prediction

In [ ]:
# Point prediction only using binary success metric (p_pt_pred)
function point_prediction(;portfolio_pool = Vector{Int64}())

    model_pp_c_nr = Model(Gurobi.Optimizer)
    set_optimizer_attribute(model_pp_c_nr, "TimeLimit", 60) # Good practice, forces solver to stop running

    #Variables
    @variable(model_pp_c_nr, x[1:n] >= 0) #How much to invest in a startup
    @variable(model_pp_c_nr, z[1:n], Bin)  # Invest or not

    #Constraints
    @constraint(model_pp_c_nr, sum(x[i] for i in 1:n) <= B) #Can't invest more than your budget
    @constraint(model_pp_c_nr, [i=1:n], x[i] <= money_raised_before_seriesB[i]) #Can't invest more in 1 startup than they raised in series B
    # @constraint(model_pp_c_nr, [i=1:n], x[i] <= 1/10 * B) #Max amount to invest in each startup #NO IMPACT IN THIS MODEL?
    # @constraint(model_pp_c_nr, sum(z[i] for i in 1:n) >= N_lower) #Min number of startups to invest in #NO IMPACT IN THIS MODEL?
    # @constraint(model_pp_c_nr, sum(z[i] for i in 1:n) <= N_upper) #Max number of startups to invest in 
    @constraint(model_pp_c_nr, [i=1:n], x[i] <= M * z[i])  # If z[i] == 0, x[i] must be 0 
    #can only invest as much as the startup eventually raised in series b

    # Apply portfolio pool constraint if not empty
    if !isempty(portfolio_pool)
        @constraint(model_pp_c_nr, [i=1:n; i ∉ portfolio_pool], z[i] == 0)  # z[i] = 0 for indices not in portfolio_pool
    end

    #Objective
    @objective(model_pp_c_nr, Max, sum(exp(point_pred_r[i]) * point_pred_p[i] * x[i] - x[i] for i in 1:n))

    #Optimize
    optimize!(model_pp_c_nr)
    is_solved_and_feasible(model_pp_c_nr)

    # Results
    if termination_status(model_pp_c_nr) == MOI.OPTIMAL || termination_status(model_pp_c_nr) == MOI.TIME_LIMIT
        investments = [value(x[i]) for i in 1:n]
        realized_profit_pp_c_nr = 0.0
        invested_startups_pp_c_nr = 0  # Counter for startups with investments
        println("Investment Strategy:")
        for i in 1:n
            if investments[i] > 0
                invested_startups_pp_c_nr += 1  # Increment counter for each investment
                profit = investments[i] * exp(y_test_continuous[i]) - investments[i] #Realized profit for startup i
                realized_profit_pp_c_nr += profit
                println("Startup ", i, ": Invested \$", investments[i], " => Realized Profit: \$", profit)
            end
        end
        println("Number of Startups Invested In: ", invested_startups_pp_c_nr)
        println("Total Investment: \$", sum(investments))
        println("Total Realized Profit: \$", realized_profit_pp_c_nr)
    else
        println("Optimization did not find an optimal solution.")
    end
    obj_pp_c_nr = objective_value(model_pp_c_nr)

    return model_pp_c_nr, obj_pp_c_nr, realized_profit_pp_c_nr, invested_startups_pp_c_nr
end
model_pp_c_nr, obj_pp_c_nr, realized_profit_pp_c_nr, invested_startups_pp_c_nr = point_prediction()

Set parameter Username
Academic license - for non-commercial use only - expires 2025-08-22
Set parameter TimeLimit to value 60
Set parameter TimeLimit to value 60
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: 11th Gen Intel(R) Core(TM) i7-1195G7 @ 2.90GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 3001 rows, 3000 columns and 6000 nonzeros
Model fingerprint: 0xb7552e5f
Variable types: 1500 continuous, 1500 integer (1500 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+06]
  Objective range  [1e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+03, 1e+09]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.
Found heuristic solution: objective -0.0000000
Found heuristic solution: objective 8667.8491939
Presolve removed 3001 rows and 3000 columns
Presolve time: 0.

(A JuMP Model
Maximization problem with:
Variables: 3000
Objective function type: AffExpr
`AffExpr`-in-`MathOptInterface.LessThan{Float64}`: 3001 constraints
`VariableRef`-in-`MathOptInterface.GreaterThan{Float64}`: 1500 constraints
`VariableRef`-in-`MathOptInterface.ZeroOne`: 1500 constraints
Model mode: AUTOMATIC
CachingOptimizer state: ATTACHED_OPTIMIZER
Solver name: Gurobi
Names registered in the model: x, z, 27328.482734338915, 18830.06535947712, 1)

## Point Prediction (w/ robustness)

In [49]:
function point_prediction_robust(;portfolio_pool = Vector{Int64}())

    Gamma = floor(Int, 0.003 * n)  # Uncertainty budget
    y = [point_pred_p[i] for i in 1:n]  # Predicted binary labels
    r = [point_pred_r[i] for i in 1:n]  # Predicted rewards

    # Model
    model_pp_c_r = Model(Gurobi.Optimizer)
    set_optimizer_attribute(model_pp_c_r, "TimeLimit", 60)  # Time limit for the solver

    # Variables
    @variable(model_pp_c_r, x[1:n] >= 0)  # Investment amounts
    @variable(model_pp_c_r, θ <= 0)  # Dual variable for uncertainty budget
    @variable(model_pp_c_r, u[1:n] >= 0)  # u variables for upward flips
    @variable(model_pp_c_r, v[1:n] >= 0)  # v variables for downward flips
    @variable(model_pp_c_r, w[1:n] <= 0)  # w variables for slack terms
    @variable(model_pp_c_r, z[1:n], Bin)  # Invest or not


    # Constraints
    # Budget constraint
    @constraint(model_pp_c_r, sum(x[i] for i in 1:n) <= B)
    @constraint(model_pp_c_r, [i=1:n], x[i] <= money_raised_before_seriesB[i]) #Can't invest more in 1 startup than they raised in series B
    # @constraint(model_pp_c_r, [i=1:n], x[i] <= 1/10 * B) #Max amount to invest in each startup #NO IMPACT IN THIS MODEL
    # @constraint(model_pp_c_r, sum(z[i] for i in 1:n) >= N_lower) #Min number of startups to invest in #NO IMPACT IN THIS MODEL
    # @constraint(model_pp_c_r, sum(z[i] for i in 1:n) <= N_upper) #Max number of startups to invest in #NO IMPACT IN THIS MODEL
    @constraint(model_pp_c_r, [i=1:n], x[i] <= M * z[i])  # If z[i] == 0, x[i] must be 0 #NO IMPACT IN THIS MODEL

    # Robust constraints
    @constraint(model_pp_c_r, [i=1:n], θ + u[i] - v[i] + w[i] <= 0)
    @constraint(model_pp_c_r, [i=1:n], u[i] + v[i] <= exp(r[i]) * x[i])

    # Apply portfolio pool constraint if not empty
    if !isempty(portfolio_pool)
        @constraint(model_pp_c_r, [i=1:n; i ∉ portfolio_pool], z[i] == 0)  # z[i] = 0 for indices not in portfolio_pool
    end

    # Objective function
    @objective(
        model_pp_c_r,
        Max,
        Gamma * θ + sum(y[i] * (u[i] - v[i]) + w[i] - x[i] for i in 1:n)  # Subtract initial investment

    )

    # Optimize
    optimize!(model_pp_c_r)

    # Results
    if termination_status(model_pp_c_r) == MOI.OPTIMAL || termination_status(model_pp_c_r) == MOI.TIME_LIMIT
        investments = [value(x[i]) for i in 1:n]
        realized_profit_pp_c_r = 0.0
        invested_startups_pp_c_r = 0  # Counter for startups with investments
        println("Investment Strategy:")
        for i in 1:n
            if investments[i] > 0
                invested_startups_pp_c_r += 1  # Increment counter for each investment
                profit = investments[i] * exp(y_test_continuous[i]) - investments[i] #Realized profit for startup i
                realized_profit_pp_c_r += profit
                println("Startup ", i, ": Invested \$", investments[i], " => Realized Profit: \$", profit)
            end
        end
        println("Number of Startups Invested In: ", invested_startups_pp_c_r)
        println("Total Investment: \$", sum(investments))
        println("Total Realized Profit: \$", realized_profit_pp_c_r)
    else
        println("Optimization did not find an optimal solution.")
    end
    obj_pp_c_r = objective_value(model_pp_c_r);

    return model_pp_c_r, obj_pp_c_r, realized_profit_pp_c_r, invested_startups_pp_c_r
end
model_pp_c_r, obj_pp_c_r, realized_profit_pp_c_r, invested_startups_pp_c_r = point_prediction_robust()

Set parameter Username
Academic license - for non-commercial use only - expires 2025-08-22
Set parameter TimeLimit to value 60
Set parameter TimeLimit to value 60
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: 11th Gen Intel(R) Core(TM) i7-1195G7 @ 2.90GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 6001 rows, 7501 columns and 16500 nonzeros
Model fingerprint: 0x8947c8a8
Variable types: 6001 continuous, 1500 integer (1500 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+06]
  Objective range  [1e+00, 4e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+03, 1e+09]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.
Found heuristic solution: objective -0.0000000
Presolve removed 5987 rows and 7487 columns
Presolve time: 0.03s
Presolved: 14 rows, 14 columns, 39 nonzeros


(A JuMP Model
Maximization problem with:
Variables: 7501
Objective function type: AffExpr
`AffExpr`-in-`MathOptInterface.LessThan{Float64}`: 6001 constraints
`VariableRef`-in-`MathOptInterface.GreaterThan{Float64}`: 4500 constraints
`VariableRef`-in-`MathOptInterface.LessThan{Float64}`: 1501 constraints
`VariableRef`-in-`MathOptInterface.ZeroOne`: 1500 constraints
Model mode: AUTOMATIC
CachingOptimizer state: ATTACHED_OPTIMIZER
Solver name: Gurobi
Names registered in the model: u, v, w, x, z, θ, 24495.634460905043, 40294.90684228846, 40)

## Weighted Average

In [52]:
function weighted_average(;portfolio_pool = Vector{Int64}())
    # Step 1: Compute avg_ry dynamically for `n` test samples
    avg_ry = [
        begin
            # Union of neighbor indices
            union_indices = unique(vcat(
                findall(train_data_continuous.Leaf_continuous .== test_data_continuous.Leaf_continuous[i]),
                findall(train_data_binary.Leaf_binary .== test_data_binary.Leaf_binary[i])
            ))

            # Extract r(u_j) and y(u_j) for the union of neighbors
            if !isempty(union_indices)
                r_values = exp.(train_data_continuous[union_indices, :log_growth])
                y_values = train_data_binary[union_indices, :Success]

                # Compute the average of r(u_j) * y(u_j)
                mean(r_values .* y_values)
            else
                0.0  # If no neighbors, return 0
            end
        end for i in 1:n
    ]
    

    # Model
    model_apr_c_nr = Model(Gurobi.Optimizer)
    set_optimizer_attribute(model_apr_c_nr, "TimeLimit", 60)  # Set a time limit

    # Variables
    @variable(model_apr_c_nr, x[1:n] >= 0)  # Investment amounts for startup i, that is in neighborhood j
    @variable(model_apr_c_nr, z[1:n], Bin)  # Invest or not

    # Constraints
    @constraint(model_apr_c_nr, sum(x[i] for i in 1:n) <= B)  # Budget constraint
    @constraint(model_apr_c_nr, [i=1:n], x[i] <= money_raised_before_seriesB[i]) #Can't invest more in 1 startup than they raised in series B
    # @constraint(model_apr_c_nr, [i=1:n], x[i] <= 1/10 * B) #Max amount to invest in each startup
    # @constraint(model_apr_c_nr, sum(z[i] for i in 1:n) >= N_lower) #Min number of startups to invest in #NO IMPACT IN THIS MODEL
    # @constraint(model_apr_c_nr, sum(z[i] for i in 1:n) <= N_upper) #Max number of startups to invest in #NO IMPACT IN THIS MODEL
    @constraint(model_apr_c_nr, [i=1:n], x[i] <= M * z[i])  # If z[i] == 0, x[i] must be 0 #NO IMPACT IN THIS MODEL

    # Apply portfolio pool constraint if not empty
    if !isempty(portfolio_pool)
        @constraint(model_apr_c_nr, [i=1:n; i ∉ portfolio_pool], z[i] == 0)  # z[i] = 0 for indices not in portfolio_pool
    end

    # Objective
    @objective(model_apr_c_nr, Max, sum(avg_ry[i] * x[i] - x[i] for i in 1:n))

    # Optimize
    optimize!(model_apr_c_nr)

    # Step 3: Evaluate Results
    if termination_status(model_apr_c_nr) == MOI.OPTIMAL || termination_status(model_apr_c_nr) == MOI.TIME_LIMIT
        investments = [value(x[i]) for i in 1:n]
        realized_profit_apr_c_nr = 0.0
        invested_startups_apr_c_nr = 0  # Counter for startups with investments
        println("Investment Strategy:")
        for i in 1:n
            if investments[i] > 0
                invested_startups_apr_c_nr += 1  # Increment counter for each investment
                profit = investments[i] * exp(y_test_continuous[i]) - investments[i]  # Realized profit for startup i
                realized_profit_apr_c_nr += profit
                println("Startup ", i, ": Invested \$", investments[i], " => Realized Profit: \$", profit)
            end
        end
        println("Number of Startups Invested In: ", invested_startups_apr_c_nr)
        println("Total Investment: \$", sum(investments))
        println("Total Realized Profit: \$", realized_profit_apr_c_nr)
    else
        println("Optimization did not find an optimal solution.")
    end
    obj_apr_c_nr = objective_value(model_apr_c_nr);

    return model_apr_c_nr, obj_apr_c_nr, realized_profit_apr_c_nr, invested_startups_apr_c_nr

end
model_apr_c_nr, obj_apr_c_nr, realized_profit_apr_c_nr, invested_startups_apr_c_nr = weighted_average()

Set parameter Username
Academic license - for non-commercial use only - expires 2025-08-22
Set parameter TimeLimit to value 60
Set parameter TimeLimit to value 60
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: 11th Gen Intel(R) Core(TM) i7-1195G7 @ 2.90GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 3001 rows, 3000 columns and 6000 nonzeros
Model fingerprint: 0x9e1c7d29
Variable types: 1500 continuous, 1500 integer (1500 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+06]
  Objective range  [3e-03, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+03, 1e+09]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.
Found heuristic solution: objective -0.0000000
Found heuristic solution: objective 17783.954164
Presolve removed 3001 rows and 3000 columns
Presolve time: 0.

(A JuMP Model
Maximization problem with:
Variables: 3000
Objective function type: AffExpr
`AffExpr`-in-`MathOptInterface.LessThan{Float64}`: 3001 constraints
`VariableRef`-in-`MathOptInterface.GreaterThan{Float64}`: 1500 constraints
`VariableRef`-in-`MathOptInterface.ZeroOne`: 1500 constraints
Model mode: AUTOMATIC
CachingOptimizer state: ATTACHED_OPTIMIZER
Solver name: Gurobi
Names registered in the model: x, z, 25376.571830182187, 158000.0, 1)

In [44]:
neighborhoods = [
        begin
            # Union of neighbor indices
            union_indices = unique(vcat(
                findall(train_data_continuous.Leaf_continuous .== test_data_continuous.Leaf_continuous[i]),
                findall(train_data_binary.Leaf_binary .== test_data_binary.Leaf_binary[i])
            ))
        end for i in 1:n
    ]
    

1500-element Vector{Vector{Int64}}:
 [41, 80, 98, 103, 105, 114, 123, 130, 143, 181  …  5974, 5975, 5979, 5982, 5983, 5988, 5992, 5993, 5994, 5997]
 [33, 44, 46, 52, 68, 71, 73, 84, 86, 91  …  5969, 5974, 5975, 5979, 5982, 5983, 5992, 5993, 5994, 5997]
 [5, 8, 38, 48, 67, 88, 146, 199, 220, 291  …  5850, 5853, 5859, 5880, 5890, 5898, 5945, 5948, 5987, 5995]
 [4, 18, 29, 47, 66, 110, 137, 157, 175, 231  …  5967, 5969, 5974, 5975, 5979, 5982, 5983, 5988, 5994, 5997]
 [17, 19, 21, 26, 27, 28, 55, 93, 99, 100  …  5967, 5969, 5974, 5975, 5979, 5982, 5988, 5992, 5993, 5994]
 [23, 87, 133, 167, 184, 186, 205, 240, 241, 271  …  5842, 5847, 5848, 5866, 5891, 5917, 5924, 5958, 5977, 5984]
 [6, 9, 13, 25, 39, 45, 49, 65, 70, 76  …  5822, 5861, 5876, 5900, 5901, 5914, 5925, 5926, 5972, 5989]
 [17, 19, 21, 26, 27, 28, 55, 93, 99, 100  …  5967, 5969, 5974, 5975, 5979, 5982, 5988, 5992, 5993, 5994]
 [6, 9, 13, 25, 39, 45, 49, 65, 70, 76  …  5928, 5941, 5960, 5966, 5968, 5973, 5990, 5991, 5996, 5998]


## Weighted Average (w/ robustness)

In [60]:
function weighted_average_robust(;portfolio_pool = Vector{Int64}())

    Gamma = floor(Int, 0.003 * n)  # Uncertainty budget

    # Step 1: Compute avg_ry dynamically for `n` test samples
    avg_ry = [
        begin
            # Union of neighbor indices
            union_indices = unique(vcat(
                findall(train_data_continuous.Leaf_continuous .== test_data_continuous.Leaf_continuous[i]),
                findall(train_data_binary.Leaf_binary .== test_data_binary.Leaf_binary[i])
            ))

            # Extract r(u_j) and y(u_j) for the union of neighbors
            if !isempty(union_indices)
                r_values = exp.(train_data_continuous[union_indices, :log_growth])
                y_values = train_data_binary[union_indices, :Success]

                # Compute the average of r(u_j) * y(u_j)
                mean(r_values .* y_values)
            else
                0.0  # If no neighbors, return 0
            end
        end for i in 1:n
    ]

    # Model
    model_apr_c_r = Model(Gurobi.Optimizer)
    set_optimizer_attribute(model_apr_c_r, "TimeLimit", 60)  # Set a time limit

    # Variables
    @variable(model_apr_c_r, x[1:n] >= 0)  # Investment amounts
    @variable(model_apr_c_r, theta >= 0)   # Dual variable for uncertainty budget
    @variable(model_apr_c_r, p[1:n] >= 0)  # Dual variables for robust constraints
    @variable(model_apr_c_r, z[1:n], Bin)  # Invest or not

    # Constraints
    @constraint(model_apr_c_r, sum(x[i] for i in 1:n) <= B)  # Budget constraint
    @constraint(model_apr_c_r, [i=1:n], x[i] <= money_raised_before_seriesB[i]) #Can't invest more in 1 startup than they raised in series B
    @constraint(model_apr_c_r, [i=1:n], -avg_ry[i] * x[i] + theta + p[i] >= 0)  # Robust dual constraints
    # @constraint(model_apr_c_r, [i=1:n], x[i] <= 1/10 * B) #Max amount to invest in each startup #NO IMPACT IN THIS MODEL
    # @constraint(model_apr_c_r, sum(z[i] for i in 1:n) >= N_lower) #Min number of startups to invest in #NO IMPACT IN THIS MODEL
    # @constraint(model_apr_c_r, sum(z[i] for i in 1:n) <= N_upper) #Max number of startups to invest in 
    @constraint(model_apr_c_r, [i=1:n], x[i] <= M * z[i])  # If z[i] == 0, x[i] must be 0

    # Apply portfolio pool constraint if not empty
    if !isempty(portfolio_pool)
        @constraint(model_apr_c_r, [i=1:n; i ∉ portfolio_pool], z[i] == 0)  # z[i] = 0 for indices not in portfolio_pool
    end

    # Objective
    @objective(model_apr_c_r, Max, sum(avg_ry[i] * x[i] - x[i] for i in 1:n) - Gamma * theta - sum(p[i] for i in 1:n))

    # Optimize
    optimize!(model_apr_c_r)

    # Step 3: Evaluate Results
    if termination_status(model_apr_c_r) == MOI.OPTIMAL || termination_status(model_apr_c_r) == MOI.TIME_LIMIT
        investments = [value(x[i]) for i in 1:n]
        realized_profit_apr_c_r = 0.0
        invested_startups_apr_c_r = 0  # Counter for startups with investments
        println("Investment Strategy:")
        for i in 1:n
            if investments[i] > 0
                invested_startups_apr_c_r += 1  # Increment counter for each investment
                profit = investments[i] * exp(y_test_continuous[i]) - investments[i]  # Realized profit for startup i
                realized_profit_apr_c_r += profit
                println("Startup ", i, ": Invested \$", investments[i], " => Realized Profit: \$", profit)
            end
        end
        println("Number of Startups Invested In: ", invested_startups_apr_c_r)
        println("Total Investment: \$", sum(investments))
        println("Total Realized Profit: \$", realized_profit_apr_c_r)
    else
        println("Optimization did not find an optimal solution.")
    end
    obj_apr_c_r = objective_value(model_apr_c_r);

    return model_apr_c_r, obj_apr_c_r, realized_profit_apr_c_r, invested_startups_apr_c_r

end
model_apr_c_r, obj_apr_c_r, realized_profit_apr_c_r, invested_startups_apr_c_r = weighted_average_robust()

Set parameter Username
Academic license - for non-commercial use only - expires 2025-08-22
Set parameter TimeLimit to value 60
Set parameter TimeLimit to value 60
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: 11th Gen Intel(R) Core(TM) i7-1195G7 @ 2.90GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 4501 rows, 4501 columns and 10500 nonzeros
Model fingerprint: 0x0053d9e0
Variable types: 3001 continuous, 1500 integer (1500 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+06]
  Objective range  [3e-03, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+03, 1e+09]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.
Found heuristic solution: objective -0.0000000
Presolve removed 4465 rows and 4462 columns
Presolve time: 0.02s
Presolved: 36 rows, 39 columns, 108 nonzeros

(A JuMP Model
Maximization problem with:
Variables: 4501
Objective function type: AffExpr
`AffExpr`-in-`MathOptInterface.GreaterThan{Float64}`: 1500 constraints
`AffExpr`-in-`MathOptInterface.LessThan{Float64}`: 3001 constraints
`VariableRef`-in-`MathOptInterface.GreaterThan{Float64}`: 3001 constraints
`VariableRef`-in-`MathOptInterface.ZeroOne`: 1500 constraints
Model mode: AUTOMATIC
CachingOptimizer state: ATTACHED_OPTIMIZER
Solver name: Gurobi
Names registered in the model: p, theta, x, z, 17836.57209370784, 23795.91694396862, 310)

# Summary Table
## Also include what constraints are used in each model (optional)
## Also see what industry each startup it invests is in, and get rank of most common industries each model invests in (optional)

In [28]:
# List of models and their names
models = [
    (model_pp_c_nr, "Point Prediction"),
    (model_pp_c_r, "Point Prediction (w/ Robustness)"),
    (model_apr_c_nr, "Weighted Average"),
    (model_apr_c_r, "Weighted Average (w/ Robustness)"),
]

# Objective values, realized profits, and invested startups
objective_values = [obj_pp_c_nr, obj_pp_c_r, obj_apr_c_nr, obj_apr_c_r]
realized_profits = [realized_profit_pp_c_nr, realized_profit_pp_c_r,
                    realized_profit_apr_c_nr, realized_profit_apr_c_r]
invested_startups = [invested_startups_pp_c_nr, invested_startups_pp_c_r,
                    invested_startups_apr_c_nr, invested_startups_apr_c_r]

using PrettyTables

# Build the DataFrame
summary_table = DataFrame(
    Model = [model[2] for model in models],  # Extract model names
    In_Sample_Profit = objective_values,
    Realized_Profit = realized_profits,
    Realized_Num_Invested_Startups = invested_startups
)

summary_table.In_Sample_Profit = round.(summary_table.In_Sample_Profit, digits=2) 
summary_table.Realized_Profit = round.(summary_table.Realized_Profit, digits=2)

# Define custom formatting functions to avoid scientific notation
formatters = (
    ft_printf("%s"),   # For Model column (default string formatting)
    ft_printf("%f"), # For In_Sample_Profit column
    ft_printf("%f"), # For Realized_Profit column
    ft_printf("%d")    # For Num_Invested_Startups column
)

# Display the summary table with PrettyTables
pretty_table(summary_table, formatters = formatters)

┌──────────────────────────────────┬──────────────────┬─────────────────┬────────────────────────────────┐
│                            Model │ In_Sample_Profit │ Realized_Profit │ Realized_Num_Invested_Startups │
│                           String │          Float64 │         Float64 │                          Int64 │
├──────────────────────────────────┼──────────────────┼─────────────────┼────────────────────────────────┤
│                 Point Prediction │         27328.48 │         28693.7 │                             10 │
│ Point Prediction (w/ Robustness) │         24495.63 │        40294.91 │                             40 │
│                 Weighted Average │         20976.13 │        62834.01 │                             10 │
│ Weighted Average (w/ Robustness) │         16917.52 │        24427.66 │                             50 │
└──────────────────────────────────┴──────────────────┴─────────────────┴────────────────────────────────┘


In [61]:
# List of models and their names
models = [
    (model_pp_c_nr, "Point Prediction"),
    (model_pp_c_r, "Point Prediction (w/ Robustness)"),
    (model_apr_c_nr, "Weighted Average"),
    (model_apr_c_r, "Weighted Average (w/ Robustness)"),
]

# Objective values, realized profits, and invested startups
objective_values = [obj_pp_c_nr, obj_pp_c_r, obj_apr_c_nr, obj_apr_c_r]
realized_profits = [realized_profit_pp_c_nr, realized_profit_pp_c_r,
                    realized_profit_apr_c_nr, realized_profit_apr_c_r]
invested_startups = [invested_startups_pp_c_nr, invested_startups_pp_c_r,
                    invested_startups_apr_c_nr, invested_startups_apr_c_r]

using PrettyTables

# Build the DataFrame
summary_table = DataFrame(
    Model = [model[2] for model in models],  # Extract model names
    In_Sample_Profit = objective_values,
    Realized_Profit = realized_profits,
    Realized_Num_Invested_Startups = invested_startups
)

summary_table.In_Sample_Profit = round.(summary_table.In_Sample_Profit, digits=2) 
summary_table.Realized_Profit = round.(summary_table.Realized_Profit, digits=2)

# Define custom formatting functions to avoid scientific notation
formatters = (
    ft_printf("%s"),   # For Model column (default string formatting)
    ft_printf("%f"), # For In_Sample_Profit column
    ft_printf("%f"), # For Realized_Profit column
    ft_printf("%d")    # For Num_Invested_Startups column
)

# Display the summary table with PrettyTables
pretty_table(summary_table, formatters = formatters)

┌──────────────────────────────────┬──────────────────┬─────────────────┬────────────────────────────────┐
│                            Model │ In_Sample_Profit │ Realized_Profit │ Realized_Num_Invested_Startups │
│                           String │          Float64 │         Float64 │                          Int64 │
├──────────────────────────────────┼──────────────────┼─────────────────┼────────────────────────────────┤
│                 Point Prediction │         27328.48 │        18830.07 │                              1 │
│ Point Prediction (w/ Robustness) │         24495.63 │        40294.91 │                             40 │
│                 Weighted Average │         25376.57 │        158000.0 │                              1 │
│ Weighted Average (w/ Robustness) │         17836.57 │        23795.92 │                            310 │
└──────────────────────────────────┴──────────────────┴─────────────────┴────────────────────────────────┘


In [70]:
# Parameters
M_portfolio = 1000  # Number of random portfolios to test
K_portfolio = 50 # Portfolio Poolsize
n_total = 1500

portfolios = [randperm(n_total)[1:K_portfolio] for _ in 1:M_portfolio]  # Random subsets of size K

df_point = Vector{Float64}()
df_weighted = Vector{Float64}()
df_robust = Vector{Float64}()
df_weighted_robust = Vector{Float64}()

for (i,portfolio) in enumerate(portfolios)
    push!(df_point, point_prediction(portfolio_pool = portfolio)[3])
    push!(df_weighted, weighted_average(portfolio_pool = portfolio)[3])
    push!(df_robust, point_prediction_robust(portfolio_pool = portfolio)[3])
    push!(df_weighted_robust, weighted_average_robust(portfolio_pool = portfolio)[3])
end


Set parameter Username
Academic license - for non-commercial use only - expires 2025-08-22
Set parameter TimeLimit to value 60
Set parameter TimeLimit to value 60
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: 11th Gen Intel(R) Core(TM) i7-1195G7 @ 2.90GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 5953 rows, 3000 columns and 11950 nonzeros
Model fingerprint: 0xeeaa2f8f
Variable types: 1500 continuous, 1500 integer (1500 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+06]
  Objective range  [1e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+01, 1e+09]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.
Found heuristic solution: objective 3202.8781931
Presolve removed 5952 rows and 2989 columns
Presolve time: 0.00s
Presolved: 1 rows, 11 columns, 11 nonzeros

Excessive output truncated after 525044 bytes.


Set parameter Username
Academic license - for non-commercial use only - expires 2025-08-22
Set parameter TimeLimit to value 60
Set parameter TimeLimit to value 60
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: 11th Gen Intel(R) Core(TM) i7-1195G7 @ 2.90GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 7453 rows, 4501 columns and 16450 nonzeros
Model fingerprint: 0xf7e7205a
Variable types: 3001 continuous, 1500 integer (1500 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+06]
  Objective range  [3e-03, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+01, 1e+09]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.
Found heuristic solution: objective -999.9999997
Presolve removed 7431 rows and 4458 columns
Presolve time: 0.00s
Presolved: 22 rows, 43 columns, 84 nonzer

In [71]:
println(describe(df_point))
println(describe(df_robust))
println(describe(df_weighted))
println(describe(df_weighted_robust))

Summary Stats:
Length:         1000
Missing Count:  0
Mean:           23417.132794
Std. Deviation: 11848.513716
Minimum:        6542.633497
1st Quartile:   15212.810682
Median:         20116.982077
3rd Quartile:   28202.491592
Maximum:        83276.399249
Type:           Float64
nothing
Summary Stats:
Length:         1000
Missing Count:  0
Mean:           11142.591553
Std. Deviation: 3357.044569
Minimum:        0.000000
1st Quartile:   9069.437791
Median:         10885.203385
3rd Quartile:   13123.869959
Maximum:        22819.429371
Type:           Float64
nothing
Summary Stats:
Length:         1000
Missing Count:  0
Mean:           23570.644332
Std. Deviation: 13026.619005
Minimum:        5394.311514
1st Quartile:   14949.930146
Median:         19498.082445
3rd Quartile:   28562.434571
Maximum:        100335.350989
Type:           Float64
nothing
Summary Stats:
Length:         1000
Missing Count:  0
Mean:           13969.296225
Std. Deviation: 7519.662484
Minimum:        4952.544432
1

In [ ]:
# Parameters
M_portfolio = 1000  # Number of random portfolios to test
K_portfolio = 10 # Portfolio Poolsize
n_total = 1500

portfolios = [randperm(n_total)[1:K_portfolio] for _ in 1:M_portfolio]  # Random subsets of size K

df_point = Vector{Float64}()
df_weighted = Vector{Float64}()
df_robust = Vector{Float64}()
df_weighted_robust = Vector{Float64}()

for (i,portfolio) in enumerate(portfolios)
    push!(df_point, point_prediction(portfolio_pool = portfolio)[3])
    push!(df_weighted, weighted_average(portfolio_pool = portfolio)[3])
    push!(df_robust, point_prediction_robust(portfolio_pool = portfolio)[3])
    push!(df_weighted_robust, weighted_average_robust(portfolio_pool = portfolio)[3])
end

Set parameter Username
Academic license - for non-commercial use only - expires 2025-08-22
Set parameter TimeLimit to value 60
Set parameter TimeLimit to value 60
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: 11th Gen Intel(R) Core(TM) i7-1195G7 @ 2.90GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 5993 rows, 3000 columns and 11990 nonzeros
Model fingerprint: 0x5f2e277c
Variable types: 1500 continuous, 1500 integer (1500 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+06]
  Objective range  [1e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+01, 1e+09]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.
Found heuristic solution: objective 6900.5323009
Presolve removed 5993 rows and 3000 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Ex

Excessive output truncated after 525436 bytes.

In [80]:
println(describe(df_point))
println(describe(df_robust))
println(describe(df_weighted))
println(describe(df_weighted_robust))

Summary Stats:
Length:         1000
Missing Count:  0
Mean:           7703.194506
Std. Deviation: 6394.522125
Minimum:        200.103033
1st Quartile:   3722.385306
Median:         5988.784914
3rd Quartile:   9590.670852
Maximum:        49882.895502
Type:           Float64
nothing
Summary Stats:
Length:         1000
Missing Count:  0
Mean:           3367.102273
Std. Deviation: 3748.043459
Minimum:        0.000000
1st Quartile:   0.000000
Median:         2757.193091
3rd Quartile:   5281.721019
Maximum:        28691.577714
Type:           Float64
nothing
Summary Stats:
Length:         1000
Missing Count:  0
Mean:           12374.642551
Std. Deviation: 19249.545558
Minimum:        1512.403507
1st Quartile:   5813.468350
Median:         8423.493290
3rd Quartile:   12389.894389
Maximum:        261281.517329
Type:           Float64
nothing
Summary Stats:
Length:         1000
Missing Count:  0
Mean:           9586.143487
Std. Deviation: 18703.278309
Minimum:        0.000000
1st Quartile:   35

In [1]:
df_point

LoadError: UndefVarError: `df_point` not defined

In [19]:
# Parameters
M_portfolio = 1000  # Number of random portfolios to test
K_portfolio = 100 # Portfolio Poolsize
n_total = 1500

portfolios = [randperm(n_total)[1:K_portfolio] for _ in 1:M_portfolio]  # Random subsets of size K

df_point = Vector{Float64}()
df_weighted = Vector{Float64}()
df_robust = Vector{Float64}()
df_weighted_robust = Vector{Float64}()

for (i,portfolio) in enumerate(portfolios)
    push!(df_point, point_prediction(portfolio_pool = portfolio)[3])
    push!(df_weighted, weighted_average(portfolio_pool = portfolio)[3])
    push!(df_robust, point_prediction_robust(portfolio_pool = portfolio)[3])
    push!(df_weighted_robust, weighted_average_robust(portfolio_pool = portfolio)[3])
end


Set parameter Username
Academic license - for non-commercial use only - expires 2025-08-22
Set parameter TimeLimit to value 60
Set parameter TimeLimit to value 60
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: 11th Gen Intel(R) Core(TM) i7-1195G7 @ 2.90GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 5903 rows, 3000 columns and 11900 nonzeros
Model fingerprint: 0xc7ceb899
Variable types: 1500 continuous, 1500 integer (1500 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+06]
  Objective range  [1e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+01, 1e+09]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.
Found heuristic solution: objective 3929.1294849
Presolve removed 5846 rows and 2891 columns
Presolve time: 0.00s
Presolved: 57 rows, 109 columns, 272 nonze

Excessive output truncated after 524930 bytes.

In [20]:
println(describe(df_point))
println(describe(df_robust))
println(describe(df_weighted))
println(describe(df_weighted_robust))

Summary Stats:
Length:         1000
Missing Count:  0
Mean:           31473.403593
Std. Deviation: 14963.877001
Minimum:        8661.384731
1st Quartile:   20515.581154
Median:         27908.232969
3rd Quartile:   37876.196246
Maximum:        94804.089986
Type:           Float64
nothing
Summary Stats:
Length:         1000
Missing Count:  0
Mean:           24914.166862
Std. Deviation: 10546.979735
Minimum:        7298.660942
1st Quartile:   17418.885012
Median:         22698.601387
3rd Quartile:   29239.340809
Maximum:        76809.587106
Type:           Float64
nothing
Summary Stats:
Length:         1000
Missing Count:  0
Mean:           26856.974090
Std. Deviation: 14738.594957
Minimum:        7727.365786
1st Quartile:   17210.349144
Median:         22046.664100
3rd Quartile:   30994.240814
Maximum:        93824.252317
Type:           Float64
nothing
Summary Stats:
Length:         1000
Missing Count:  0
Mean:           17053.806761
Std. Deviation: 4487.720751
Minimum:        7301.0404

## No Replacement

In [62]:
# Parameters
#M_portfolio = 1000  # Number of random portfolios to test
K_portfolio = 10 # Portfolio Poolsize
n_total = 1500

portfolios = [((i - 1) * K_portfolio + 1):(i * K_portfolio) for i in 1:div(n_total, K_portfolio)]

df_point = Vector{Float64}()
df_weighted = Vector{Float64}()
df_robust = Vector{Float64}()
df_weighted_robust = Vector{Float64}()

for (i,portfolio) in enumerate(portfolios)
    push!(df_point, point_prediction(portfolio_pool = portfolio)[3])
    push!(df_weighted, weighted_average(portfolio_pool = portfolio)[3])
    push!(df_robust, point_prediction_robust(portfolio_pool = portfolio)[3])
    push!(df_weighted_robust, weighted_average_robust(portfolio_pool = portfolio)[3])
end

Set parameter Username
Academic license - for non-commercial use only - expires 2025-08-22
Set parameter TimeLimit to value 60
Set parameter TimeLimit to value 60
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: 11th Gen Intel(R) Core(TM) i7-1195G7 @ 2.90GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 4491 rows, 3000 columns and 7490 nonzeros
Model fingerprint: 0x827597e4
Variable types: 1500 continuous, 1500 integer (1500 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+06]
  Objective range  [1e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+03, 1e+09]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.
Found heuristic solution: objective -0.0000000
Found heuristic solution: objective 8667.8491939
Presolve removed 4491 rows and 3000 columns
Presolve time: 0.

Excessive output truncated after 525488 bytes.

Set parameter Username
Academic license - for non-commercial use only - expires 2025-08-22
Set parameter TimeLimit to value 60
Set parameter TimeLimit to value 60
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: 11th Gen Intel(R) Core(TM) i7-1195G7 @ 2.90GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 4491 rows, 3000 columns and 7490 nonzeros
Model fingerprint: 0x047db099
Variable types: 1500 continuous, 1500 integer (1500 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+06]
  Objective range  [3e-03, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+03, 1e+09]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.
Found heuristic solution: objective -0.0000000
Found heuristic solution: objective 3588.2962433
Presolve removed 4491 rows and 3000 columns
Presolve time: 0.

In [63]:
println(describe(df_point))
println(describe(df_robust))
println(describe(df_weighted))
println(describe(df_weighted_robust))

Summary Stats:
Length:         150
Missing Count:  0
Mean:           27618.057319
Std. Deviation: 46786.186086
Minimum:        0.000000
1st Quartile:   7265.666817
Median:         14925.000000
3rd Quartile:   29674.478827
Maximum:        434120.204604
Type:           Float64
nothing
Summary Stats:
Length:         150
Missing Count:  0
Mean:           7460.593115
Std. Deviation: 7434.169332
Minimum:        0.000000
1st Quartile:   0.000000
Median:         7072.664782
3rd Quartile:   11063.533929
Maximum:        44813.969099
Type:           Float64
nothing
Summary Stats:
Length:         150
Missing Count:  0
Mean:           25202.442103
Std. Deviation: 47369.317018
Minimum:        1063.071040
1st Quartile:   6796.450210
Median:         14545.739475
3rd Quartile:   25019.954704
Maximum:        434120.204604
Type:           Float64
nothing
Summary Stats:
Length:         150
Missing Count:  0
Mean:           11521.069704
Std. Deviation: 12326.955226
Minimum:        0.000000
1st Quartile:   

In [64]:
# Parameters
#M_portfolio = 1000  # Number of random portfolios to test
K_portfolio = 50 # Portfolio Poolsize
n_total = 1500

portfolios = [((i - 1) * K_portfolio + 1):(i * K_portfolio) for i in 1:div(n_total, K_portfolio)]

df_point = Vector{Float64}()
df_weighted = Vector{Float64}()
df_robust = Vector{Float64}()
df_weighted_robust = Vector{Float64}()

for (i,portfolio) in enumerate(portfolios)
    push!(df_point, point_prediction(portfolio_pool = portfolio)[3])
    push!(df_weighted, weighted_average(portfolio_pool = portfolio)[3])
    push!(df_robust, point_prediction_robust(portfolio_pool = portfolio)[3])
    push!(df_weighted_robust, weighted_average_robust(portfolio_pool = portfolio)[3])
end
println(describe(df_point))
println(describe(df_robust))
println(describe(df_weighted))
println(describe(df_weighted_robust))

Set parameter Username
Academic license - for non-commercial use only - expires 2025-08-22
Set parameter TimeLimit to value 60
Set parameter TimeLimit to value 60
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: 11th Gen Intel(R) Core(TM) i7-1195G7 @ 2.90GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 4451 rows, 3000 columns and 7450 nonzeros
Model fingerprint: 0x5a32b9f5
Variable types: 1500 continuous, 1500 integer (1500 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+06]
  Objective range  [1e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+03, 1e+09]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.
Found heuristic solution: objective -0.0000000
Found heuristic solution: objective 8667.8491939
Presolve removed 4451 rows and 3000 columns
Presolve time: 0.

In [65]:
# Parameters
#M_portfolio = 1000  # Number of random portfolios to test
K_portfolio = 100 # Portfolio Poolsize
n_total = 1500

portfolios = [((i - 1) * K_portfolio + 1):(i * K_portfolio) for i in 1:div(n_total, K_portfolio)]

df_point = Vector{Float64}()
df_weighted = Vector{Float64}()
df_robust = Vector{Float64}()
df_weighted_robust = Vector{Float64}()

for (i,portfolio) in enumerate(portfolios)
    push!(df_point, point_prediction(portfolio_pool = portfolio)[3])
    push!(df_weighted, weighted_average(portfolio_pool = portfolio)[3])
    push!(df_robust, point_prediction_robust(portfolio_pool = portfolio)[3])
    push!(df_weighted_robust, weighted_average_robust(portfolio_pool = portfolio)[3])
end
println(describe(df_point))
println(describe(df_robust))
println(describe(df_weighted))
println(describe(df_weighted_robust))

Set parameter Username
Academic license - for non-commercial use only - expires 2025-08-22
Set parameter TimeLimit to value 60
Set parameter TimeLimit to value 60
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: 11th Gen Intel(R) Core(TM) i7-1195G7 @ 2.90GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 4401 rows, 3000 columns and 7400 nonzeros
Model fingerprint: 0x221516f2
Variable types: 1500 continuous, 1500 integer (1500 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+06]
  Objective range  [1e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+03, 1e+09]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.
Found heuristic solution: objective -0.0000000
Found heuristic solution: objective 8667.8491939
Presolve removed 4401 rows and 3000 columns
Presolve time: 0.

In [66]:
portfolios

15-element Vector{UnitRange{Int64}}:
 1:100
 101:200
 201:300
 301:400
 401:500
 501:600
 601:700
 701:800
 801:900
 901:1000
 1001:1100
 1101:1200
 1201:1300
 1301:1400
 1401:1500